In [1]:
from Evaluation.find_ranking_citation import CitationRanking
from sklearn.metrics.pairwise import linear_kernel
from Evaluation.write_result import WriteResult
from data_loading_ginny import DataLoading
from Evaluation.mean_reciprocal_ranking import MRR
from  Evaluation.eval_Ginny import Metrics
from Rec_configuraiton import Rec_configuration 
#from reranking.re_ranking_title import ReRankingTitle
#advanced deep learning stuff
import torch
#from bert_serving.client import BertClient
import pickle
from collections import defaultdict
import numpy as np
import scipy
from sentence_transformers import SentenceTransformer
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

/home/jzhu/.conda/envs/py36/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/jzhu/.conda/envs/py36/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/jzhu/.conda/envs/py36/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/jzhu/.conda/envs/py36/lib/python3.6/site-packages/tensorflow/

In [2]:
torch.cuda.current_device()
#torch.cuda.device(0)

0

In [3]:
torch.cuda.device_count()

2

In [4]:
print(torch.cuda.get_device_name(0))
print(torch.cuda.get_device_name(1))

Tesla V100-PCIE-16GB
Tesla V100-PCIE-16GB


In [2]:
torch.cuda.set_device(1)

In [7]:
class Master:
    def __init__(self, rerank = False):
        self.rec_conf = Rec_configuration()
        self.article_title, self.article_abstract, self.geo_title, \
        self.geo_summary, self.citation_data = DataLoading().get_all_details() #we should get actual citations
        self.auto_rank = CitationRanking(self.citation_data)
        self.write_res = WriteResult()
     
        '''
        #later we're gonna test on all datasets that has referenced paper 
        self.geo_test_data = ["GSE20361", "GSE23137", "GSE1640", "GSE41034", "GSE1864", "GSE44700", "GSE50988"]#, \
                              #"GSE46045", "GSE32869", "GSE22955", "GSE41072", "GSE50624", "GSE18684", "GSE770", \
                              #"GSE9048", "GSE9854", "GSE23135", "GSE23136", "GSE23139", "GSE49583", "GSE49584", \
                              #"GSE49586", "GSE64073", "GSE38623", "GSE3113", "GSE41491", "GSE29641", "GSE26002", \
                              #"GSE17018", "GSE71121", "GSE21618", "GSE23138", "GSE20988", "GSE52710", "GSE14103", \
                              #"GSE53294"] #36
        '''
        #or,
        choose = list(self.citation_data.keys())
        self.geo_test_data = [key for key in choose if self.citation_data[key] != []] #76,064
        #self.rr = ReRankingTitle() # i definitely need to work on this as well (re-ranking title using bert)
        self.top_threshold = 10 #sounds nice
        self.rerank = rerank
        #bert related
        self.model_distilbert = SentenceTransformer('distilbert-base-nli-stsb-mean-tokens') #roberta 
        #self.model_addr = self.rec_conf.model_path_roberta #subject to change
        self.res_addr = self.rec_conf.result_address_distilbert #subject to change

        
    def re_rank_bert(self, geo_sim_dict, article_title, geo_title, pmid_ls): #pmid_ls. should be the complete pmid: similarity score column dimension
        assert np.asarray(list(geo_sim_dict.values())).shape[1] == len(pmid_ls) #the # of columns should be equal to total # of pmids
        geo_words = list(geo_title.values())#a list of words? I don't need to split for bert
        title_words = list(article_title.values())
        sim_value = linear_kernel(self.model_bert.encode(geo_words), self.model_bert.encode(title_words))
        for i, geo_id in enumerate(geo_sim_dict): #key of the dictionary is the geo-ids
            #for each geo_id, adding re-ranking values
            geo_sim_dict[geo_id] += sim_value[i, :]
        return self.sorting(geo_sim_dict, pmid_ls)
    
    def sorting(self, geo_sim_dict, pmid_ls):
          
        '''
        for each geo_id, give a list of recommendations 
        this could be for non-reranking or reranking
        '''
        similarity_dict = defaultdict()
        sim_np = np.asarray(list(geo_sim_dict.values()))
        idx_np = np.argsort(-sim_np, axis= 1) #so the big values will be in front 
        #take on # of top_threshold
        idx_np = idx_np[:,:self.top_threshold]
        sim_np_taketop = np.take_along_axis(sim_np, idx_np, axis=1) 
        for i, geo_id in enumerate(geo_sim_dict):
            pmid_selected = list(np.take(pmid_ls, idx_np[i]))
            selected = dict(zip(pmid_selected, sim_np_taketop[i]))
            similarity_dict[geo_id] = selected     
        return similarity_dict
    
    def process(self):
        #check paths and check vecs        
        pmids, distilbert_vecs = None, None #this should be loading something

        # This is for loading the pre-trained bert models.
        if distilbert_vecs is not None and pmids is not None:
            print('load trained models and encoded publications vectors')
            '''
            
            '''
        else:
            print('Building models')
            joined_dict_article = {}
            for pmid in self.article_title: #for articles, encoding the articles
                #print('pmid')
                #print(pmid)
                if (self.article_title[pmid] + self.article_abstract[pmid]).strip() != '':
                    joined_dict_article[pmid] = self.article_title[pmid] + ' ' + self.article_abstract[pmid]
            #should be some training here, otherwise just do the easiest encodinh
            pmids, distilbert_vecs = list(joined_dict_article.keys()), self.model_distilbert.encode(list(joined_dict_article.values()))
            with open(self.res_addr + 'base/distilbert_vecs', 'wb') as handle:
                pickle.dump(distilbert_vecs, handle, protocol=pickle.HIGHEST_PROTOCOL)
            with open(self.res_addr + 'base/pmids', 'wb') as handle:
                pickle.dump(pmids, handle, protocol=pickle.HIGHEST_PROTOCOL)
        
        #keep only articles with non-zero values
        #new_article_abstract = {new_key: self.article_abstract[new_key] for new_key in pmids} #770,525
        #new_article_title = {new_key: self.article_title[new_key] for new_key in pmids}
   
    
        joined_dict_geo = {} # maxium: 76,064
        # screening first for those geo_ids with pmids 
        for geo_id in self.geo_test_data:
            print('geo_id')
            print(geo_id)
            if (self.geo_title[geo_id] + self.geo_summary[geo_id]).strip() != '':
                #only get the ones with actual texts
                joined_dict_geo[geo_id] = self.geo_title[geo_id] + ' ' + self.geo_summary[geo_id]
        geo_ids, geo_distilbert_vecs = list(joined_dict_geo.keys()), self.model_distilbert.encode(list(joined_dict_geo.values()))
        with open(self.res_addr + 'base/geo_distilbert_vecs', 'wb') as handle:
            pickle.dump(geo_distilbert_vecs, handle, protocol=pickle.HIGHEST_PROTOCOL)
        with open(self.res_addr + 'base/geo_ids', 'wb') as handle:
            pickle.dump(geo_ids, handle, protocol=pickle.HIGHEST_PROTOCOL)        
        
        #with open(self.res_addr + 'parrot.pkl', 'wb') as f:
            #pickle.dump(mylist, f)
        #keep only geo datasets with non-zero values
        #new_geo_summary = {new_key: self.geo_summary[new_key] for new_key in geo_ids} #770,525
        #new_geo_title = {new_key: self.geo_title[new_key] for new_key in geo_ids}
        
        """
        similarity_value_dict = defaultdict()
        similarity_scores = linear_kernel(geo_bert_vecs, bert_vecs)
        #we need to export this value
        np.save(self.res_addr + 'base/similarity_scores', similarity_scores)
        #load this later
        #np.load(self.res_addr + 'base/similarity_scores')
        print(similarity_scores.shape)
        #call the re-ranking or not 
        for i, geo_id in enumerate(geo_ids): #this is only from testing geo_id
            print(geo_id)
            #print(geo_id)
            similarity_value_dict[geo_id] =  list(similarity_scores[i])
            #similarity_value_dict[geo_id] = scipy.spatial.distance.cdist([geo_bert_vecs[i]], bert_vecs, "cosine")[0]
        if self.rerank:
            new_similarity_dict = self.re_rank_bert(geo_sim_dict = similarity_value_dict,
                                                       article_title = new_article_title,
                                                       geo_title = new_geo_title, 
                                                       pmid_ls = pmids)
        else:
            new_similarity_dict =  self.sorting(geo_sim_dict = similarity_value_dict, pmid_ls = pmids)
        
        with open(self.res_addr + 'base/new_similarity_dict.pickle', 'wb') as handle:
            pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)
        
        
        #screen for geo_ids that actually has citations t
        for id, geo_id in enumerate(geo_ids): 
            #this has already stored in a pickled list of geo_haspmid.pickle
            temp_selected = new_similarity_dict[geo_id]
            #modify this later based on rerank or base; plain or futher trained
            if self.rerank:
                self.write_res.write(self.res_addr + 'rerank/'  + geo_id + '.txt', temp_selected)
            else:
                #we will have things here this time. 
                self.write_res.write(self.res_addr + 'base/'  + geo_id + '.txt', temp_selected)
            self.auto_rank.find_citations(geo_id, list(temp_selected.keys())) #keys are a list of pmids
            
        a, b, c, d = self.auto_rank.get_values() #need to modify this 
        print('good geo recommendations = {}, top1 hit geo recommendations = {}, bad geo recommendations = {}, '
              'geo without citations = {}'.format(a, b, c, d))
        #we need many more than just MRR
        #MRR 
        print('MRR')
        print(Metrics(self.citation_data).calculate_mrr(new_similarity_dict)) #mrr
        #recall @1 and recall @10
        print('recall@1, recall@10')
        print(Metrics(self.citation_data).calculate_recall_at_k(similarity_dict, 1))
        print(Metrics(self.citation_data).calculate_recall_at_k(similarity_dict, 10))
        #Precision@1 and precision10
        print('precision@1, precision@10')
        print(Metrics(self.citation_data).calculate_precision_at_k(similarity_dict, 1))        
        print(Metrics(self.citation_data).calculate_precision_at_k(similarity_dict, 10))
        #MAP@10
        print(Metrics(self.citation_data).calculate_calculate_MAP_at_k(similarity_dict))
        """

In [8]:
def main():
    x = Master(rerank = False)
    x.process()


if __name__ == '__main__':
    main()

Lemmatization is false, if required turn on again
Loading all geo related preprocessed datasets
Loaded all geo related processed datasets
Loading all title and abstract
Loaded all title and abstract
Building models
geo_id
GSE103837
geo_id
GSE89809
geo_id
GSE11663
geo_id
GSE55127
geo_id
GSE61914
geo_id
GSE96174
geo_id
GSE108140
geo_id
GSE55064
geo_id
GSE77553
geo_id
GSE836
geo_id
GSE48997
geo_id
GSE4248
geo_id
GSE71695
geo_id
GSE16495
geo_id
GSE92231
geo_id
GSE36779
geo_id
GSE28180
geo_id
GSE93962
geo_id
GSE97290
geo_id
GSE76313
geo_id
GSE27104
geo_id
GSE78579
geo_id
GSE33842
geo_id
GSE96211
geo_id
GSE92438
geo_id
GSE27139
geo_id
GSE25518
geo_id
GSE72425
geo_id
GSE96905
geo_id
GSE8547
geo_id
GSE12256
geo_id
GSE76217
geo_id
GSE43669
geo_id
GSE10903
geo_id
GSE102695
geo_id
GSE105628
geo_id
GSE72212
geo_id
GSE44657
geo_id
GSE92332
geo_id
GSE81888
geo_id
GSE4500
geo_id
GSE83148
geo_id
GSE32214
geo_id
GSE70328
geo_id
GSE81569
geo_id
GSE55869
geo_id
GSE65781
geo_id
GSE37546
geo_id
GSE89581
ge

geo_id
GSE50035
geo_id
GSE679
geo_id
GSE105533
geo_id
GSE70216
geo_id
GSE39694
geo_id
GSE35570
geo_id
GSE2982
geo_id
GSE84688
geo_id
GSE71904
geo_id
GSE106962
geo_id
GSE20415
geo_id
GSE63581
geo_id
GSE90655
geo_id
GSE83185
geo_id
GSE95666
geo_id
GSE3181
geo_id
GSE39911
geo_id
GSE78563
geo_id
GSE14320
geo_id
GSE25057
geo_id
GSE73068
geo_id
GSE9563
geo_id
GSE47592
geo_id
GSE68627
geo_id
GSE16609
geo_id
GSE80293
geo_id
GSE38962
geo_id
GSE31502
geo_id
GSE97109
geo_id
GSE88016
geo_id
GSE77389
geo_id
GSE6432
geo_id
GSE79579
geo_id
GSE84172
geo_id
GSE102954
geo_id
GSE61388
geo_id
GSE71019
geo_id
GSE87305
geo_id
GSE42736
geo_id
GSE35490
geo_id
GSE34223
geo_id
GSE56400
geo_id
GSE32680
geo_id
GSE82282
geo_id
GSE79049
geo_id
GSE18201
geo_id
GSE93451
geo_id
GSE49690
geo_id
GSE92033
geo_id
GSE104614
geo_id
GSE84791
geo_id
GSE19434
geo_id
GSE55709
geo_id
GSE82697
geo_id
GSE27038
geo_id
GSE62008
geo_id
GSE68952
geo_id
GSE105672
geo_id
GSE89915
geo_id
GSE28349
geo_id
GSE33446
geo_id
GSE2512
geo_id
GSE

GSE34386
geo_id
GSE117628
geo_id
GSE53531
geo_id
GSE78347
geo_id
GSE25297
geo_id
GSE45776
geo_id
GSE66525
geo_id
GSE64835
geo_id
GSE105704
geo_id
GSE103100
geo_id
GSE11436
geo_id
GSE100247
geo_id
GSE88795
geo_id
GSE81836
geo_id
GSE54857
geo_id
GSE19041
geo_id
GSE22155
geo_id
GSE80970
geo_id
GSE6061
geo_id
GSE840
geo_id
GSE58218
geo_id
GSE48346
geo_id
GSE58396
geo_id
GSE32513
geo_id
GSE88676
geo_id
GSE64814
geo_id
GSE58918
geo_id
GSE11788
geo_id
GSE52252
geo_id
GSE105845
geo_id
GSE73803
geo_id
GSE42003
geo_id
GSE38306
geo_id
GSE4217
geo_id
GSE28272
geo_id
GSE25138
geo_id
GSE62825
geo_id
GSE56442
geo_id
GSE63486
geo_id
GSE12215
geo_id
GSE1778
geo_id
GSE88486
geo_id
GSE90238
geo_id
GSE94617
geo_id
GSE30831
geo_id
GSE35049
geo_id
GSE53603
geo_id
GSE110270
geo_id
GSE38063
geo_id
GSE504
geo_id
GSE36274
geo_id
GSE70954
geo_id
GSE48351
geo_id
GSE105514
geo_id
GSE52440
geo_id
GSE103011
geo_id
GSE90137
geo_id
GSE89696
geo_id
GSE5058
geo_id
GSE84402
geo_id
GSE45975
geo_id
GSE68596
geo_id
GSE24937

geo_id
GSE58148
geo_id
GSE82031
geo_id
GSE99866
geo_id
GSE82707
geo_id
GSE40024
geo_id
GSE17166
geo_id
GSE21900
geo_id
GSE104346
geo_id
GSE26544
geo_id
GSE73980
geo_id
GSE58547
geo_id
GSE84141
geo_id
GSE39058
geo_id
GSE74914
geo_id
GSE60660
geo_id
GSE88308
geo_id
GSE32162
geo_id
GSE25042
geo_id
GSE74019
geo_id
GSE104907
geo_id
GSE59736
geo_id
GSE10166
geo_id
GSE45161
geo_id
GSE4804
geo_id
GSE12336
geo_id
GSE47054
geo_id
GSE71134
geo_id
GSE57025
geo_id
GSE77491
geo_id
GSE25232
geo_id
GSE13747
geo_id
GSE17274
geo_id
GSE29948
geo_id
GSE55509
geo_id
GSE41280
geo_id
GSE35008
geo_id
GSE97680
geo_id
GSE49864
geo_id
GSE69241
geo_id
GSE35378
geo_id
GSE51133
geo_id
GSE88416
geo_id
GSE26838
geo_id
GSE61743
geo_id
GSE2712
geo_id
GSE27913
geo_id
GSE41240
geo_id
GSE20209
geo_id
GSE42341
geo_id
GSE13443
geo_id
GSE44402
geo_id
GSE18589
geo_id
GSE63507
geo_id
GSE77039
geo_id
GSE99309
geo_id
GSE4952
geo_id
GSE93858
geo_id
GSE78570
geo_id
GSE26248
geo_id
GSE83776
geo_id
GSE109764
geo_id
GSE96761
geo_id
G

geo_id
GSE111042
geo_id
GSE82084
geo_id
GSE56787
geo_id
GSE24568
geo_id
GSE57767
geo_id
GSE54679
geo_id
GSE32381
geo_id
GSE36355
geo_id
GSE34242
geo_id
GSE31911
geo_id
GSE55365
geo_id
GSE88945
geo_id
GSE51793
geo_id
GSE1936
geo_id
GSE86463
geo_id
GSE25785
geo_id
GSE36970
geo_id
GSE31598
geo_id
GSE59394
geo_id
GSE81764
geo_id
GSE99498
geo_id
GSE29888
geo_id
GSE65787
geo_id
GSE87714
geo_id
GSE8301
geo_id
GSE27290
geo_id
GSE82959
geo_id
GSE53006
geo_id
GSE2508
geo_id
GSE2539
geo_id
GSE71109
geo_id
GSE43233
geo_id
GSE94295
geo_id
GSE106092
geo_id
GSE66171
geo_id
GSE18992
geo_id
GSE6987
geo_id
GSE106721
geo_id
GSE19201
geo_id
GSE25278
geo_id
GSE78309
geo_id
GSE4034
geo_id
GSE94434
geo_id
GSE47061
geo_id
GSE91056
geo_id
GSE82808
geo_id
GSE20347
geo_id
GSE15806
geo_id
GSE10151
geo_id
GSE84498
geo_id
GSE78705
geo_id
GSE48006
geo_id
GSE96349
geo_id
GSE31985
geo_id
GSE16008
geo_id
GSE4478
geo_id
GSE62222
geo_id
GSE71081
geo_id
GSE30543
geo_id
GSE90235
geo_id
GSE33995
geo_id
GSE91241
geo_id
GSE61

...

GSE52431
geo_id
GSE54955
geo_id
GSE54204
geo_id
GSE91595
geo_id
GSE10464
geo_id
GSE82749
geo_id
GSE89672
geo_id
GSE1577
geo_id
GSE37558
geo_id
GSE63726
geo_id
GSE83718
geo_id
GSE24546
geo_id
GSE67311
geo_id
GSE85173
geo_id
GSE28237
geo_id
GSE21446
geo_id
GSE85072
geo_id
GSE34139
geo_id
GSE48147
geo_id
GSE86130
geo_id
GSE8969
geo_id
GSE12444
geo_id
GSE84244
geo_id
GSE12247
geo_id
GSE12595
geo_id
GSE112753
geo_id
GSE13278
geo_id
GSE45818
geo_id
GSE58605
geo_id
GSE13609
geo_id
GSE65505
geo_id
GSE66507
geo_id
GSE11690
geo_id
GSE42033
geo_id
GSE50821
geo_id
GSE90395
geo_id
GSE3696
geo_id
GSE28656
geo_id
GSE53760
geo_id
GSE607
geo_id
GSE13069
geo_id
GSE33677
geo_id
GSE43462
geo_id
GSE11486
geo_id
GSE12868
geo_id
GSE20224
geo_id
GSE74550
geo_id
GSE9726
geo_id
GSE55027
geo_id
GSE56138
geo_id
GSE53181
geo_id
GSE35763
geo_id
GSE54523
geo_id
GSE41256
geo_id
GSE76590
geo_id
GSE90418
geo_id
GSE19877
geo_id
GSE32716
geo_id
GSE45237
geo_id
GSE101487
geo_id
GSE57182
geo_id
GSE83893
geo_id
GSE83271
geo

geo_id
GSE60244
geo_id
GSE19964
geo_id
GSE44744
geo_id
GSE19365
geo_id
GSE27854
geo_id
GSE18096
geo_id
GSE45579
geo_id
GSE84358
geo_id
GSE70241
geo_id
GSE6528
geo_id
GSE96026
geo_id
GSE13155
geo_id
GSE46492
geo_id
GSE68022
geo_id
GSE58168
geo_id
GSE53791
geo_id
GSE23790
geo_id
GSE16603
geo_id
GSE62503
geo_id
GSE51854
geo_id
GSE9577
geo_id
GSE88201
geo_id
GSE32427
geo_id
GSE69192
geo_id
GSE100416
geo_id
GSE10833
geo_id
GSE18256
geo_id
GSE89683
geo_id
GSE58032
geo_id
GSE19875
geo_id
GSE43730
geo_id
GSE34946
geo_id
GSE42721
geo_id
GSE59209
geo_id
GSE67051
geo_id
GSE53070
geo_id
GSE105670
geo_id
GSE63336
geo_id
GSE2890
geo_id
GSE4339
geo_id
GSE81102
geo_id
GSE16222
geo_id
GSE8249
geo_id
GSE81707
geo_id
GSE42449
geo_id
GSE74053
geo_id
GSE17845
geo_id
GSE88223
geo_id
GSE6714
geo_id
GSE114290
geo_id
GSE39435
geo_id
GSE28597
geo_id
GSE92008
geo_id
GSE6092
geo_id
GSE34501
geo_id
GSE5660
geo_id
GSE37484
geo_id
GSE72200
geo_id
GSE14873
geo_id
GSE80424
geo_id
GSE66793
geo_id
GSE2387
geo_id
GSE1377

geo_id
GSE34720
geo_id
GSE107225
geo_id
GSE42995
geo_id
GSE96753
geo_id
GSE28071
geo_id
GSE85507
geo_id
GSE78099
geo_id
GSE6928
geo_id
GSE75985
geo_id
GSE40495
geo_id
GSE92949
geo_id
GSE76511
geo_id
GSE26664
geo_id
GSE78612
geo_id
GSE9804
geo_id
GSE68018
geo_id
GSE53054
geo_id
GSE23609
geo_id
GSE31898
geo_id
GSE33875
geo_id
GSE251
geo_id
GSE7848
geo_id
GSE8769
geo_id
GSE53595
geo_id
GSE65033
geo_id
GSE78102
geo_id
GSE27683
geo_id
GSE51043
geo_id
GSE39620
geo_id
GSE33070
geo_id
GSE65577
geo_id
GSE4817
geo_id
GSE52447
geo_id
GSE53784
geo_id
GSE84920
geo_id
GSE38007
geo_id
GSE47387
geo_id
GSE105800
geo_id
GSE106313
geo_id
GSE44935
geo_id
GSE85125
geo_id
GSE112764
geo_id
GSE11360
geo_id
GSE46708
geo_id
GSE2822
geo_id
GSE56623
geo_id
GSE71774
geo_id
GSE32227
geo_id
GSE18225
geo_id
GSE86310
geo_id
GSE81991
geo_id
GSE66137
geo_id
GSE29353
geo_id
GSE6313
geo_id
GSE88244
geo_id
GSE63732
geo_id
GSE39276
geo_id
GSE51588
geo_id
GSE49859
geo_id
GSE90117
geo_id
GSE42936
geo_id
GSE105239
geo_id
GSE31

geo_id
GSE10159
geo_id
GSE37397
geo_id
GSE49962
geo_id
GSE81482
geo_id
GSE28243
geo_id
GSE14857
geo_id
GSE91879
geo_id
GSE29810
geo_id
GSE84123
geo_id
GSE85060
geo_id
GSE49573
geo_id
GSE8523
geo_id
GSE35900
geo_id
GSE75862
geo_id
GSE82791
geo_id
GSE102736
geo_id
GSE37234
geo_id
GSE52766
geo_id
GSE82513
geo_id
GSE43106
geo_id
GSE4890
geo_id
GSE19597
geo_id
GSE102334
geo_id
GSE71662
geo_id
GSE46646
geo_id
GSE15653
geo_id
GSE16207
geo_id
GSE71107
geo_id
GSE23056
geo_id
GSE51257
geo_id
GSE106889
geo_id
GSE102399
geo_id
GSE41097
geo_id
GSE71119
geo_id
GSE41942
geo_id
GSE88964
geo_id
GSE4563
geo_id
GSE28685
geo_id
GSE5045
geo_id
GSE71232
geo_id
GSE23601
geo_id
GSE59321
geo_id
GSE6728
geo_id
GSE15395
geo_id
GSE66166
geo_id
GSE3751
geo_id
GSE105520
geo_id
GSE36489
geo_id
GSE44571
geo_id
GSE16331
geo_id
GSE88692
geo_id
GSE77299
geo_id
GSE79032
geo_id
GSE55575
geo_id
GSE104410
geo_id
GSE2879
geo_id
GSE104947
geo_id
GSE42267
geo_id
GSE71378
geo_id
GSE28248
geo_id
GSE30593
geo_id
GSE20273
geo_id
G

geo_id
GSE18054
geo_id
GSE78421
geo_id
GSE4644
geo_id
GSE61100
geo_id
GSE57820
geo_id
GSE6653
geo_id
GSE36343
geo_id
GSE24839
geo_id
GSE105849
geo_id
GSE60364
geo_id
GSE9589
geo_id
GSE27240
geo_id
GSE95591
geo_id
GSE75369
geo_id
GSE906
geo_id
GSE31648
geo_id
GSE72934
geo_id
GSE21659
geo_id
GSE22269
geo_id
GSE91909
geo_id
GSE22720
geo_id
GSE75368
geo_id
GSE83311
geo_id
GSE11386
geo_id
GSE61848
geo_id
GSE7326
geo_id
GSE43912
geo_id
GSE55974
geo_id
GSE101516
geo_id
GSE106786
geo_id
GSE37233
geo_id
GSE2816
geo_id
GSE30073
geo_id
GSE75982
geo_id
GSE82685
geo_id
GSE88620
geo_id
GSE50395
geo_id
GSE36586
geo_id
GSE87102
geo_id
GSE90321
geo_id
GSE80875
geo_id
GSE40246
geo_id
GSE105024
geo_id
GSE34001
geo_id
GSE68197
geo_id
GSE97487
geo_id
GSE38631
geo_id
GSE9135
geo_id
GSE93816
geo_id
GSE54314
geo_id
GSE64553
geo_id
GSE30258
geo_id
GSE36667
geo_id
GSE109628
geo_id
GSE77705
geo_id
GSE74001
geo_id
GSE81737
geo_id
GSE5474
geo_id
GSE20493
geo_id
GSE95899
geo_id
GSE3202
geo_id
GSE21741
geo_id
GSE261

In [3]:
#read-in stored vec 
res_addr = 'results/distilbert_plain/base/'
with open(res_addr +'distilbert_vecs', 'rb') as fp:
    distilbert_vecs = pickle.load(fp)
with open(res_addr +'geo_distilbert_vecs', 'rb') as fp:
      geo_distilbert_vecs = pickle.load(fp)        
        
with open(res_addr +'pmids', 'rb') as fp:
      pmids = pickle.load(fp)
with open(res_addr +'geo_ids', 'rb') as fp:
      geo_ids = pickle.load(fp)      
        
        
distilbert_vecs = torch.tensor(np.array(distilbert_vecs)).cuda()
#pmids = torch.tensor(pmids).cuda()


geo_distilbert_vecs = torch.tensor(np.array(geo_distilbert_vecs))
#geo_ids = torch.tensor(geo_ids)

In [9]:
from sklearn import preprocessing
le = preprocessing.LabelEncoder()
targets = le.fit_transform(['cat','dog', 'more'])
le.classes_
#array([1, 2, 6])
le.transform(['cat','dog', 'more'])
#array([0, 0, 1, 2]...)
print(le.inverse_transform([0, 0, 1, 2])
array([1, 1, 2, 6])

In [4]:
print(pmids[:2])
geo_ids[:2]

['25240462', '20122219']


['GSE103837', 'GSE89809']

In [5]:
b_size = 64
geo_distilbert_vecs_data = TensorDataset(geo_distilbert_vecs)
geo_distilbert_vecs_sampler = SequentialSampler(geo_distilbert_vecs_data) #sequential here 
geo_distilbert_vecs_dataloader = DataLoader(geo_distilbert_vecs_data, sampler=geo_distilbert_vecs_sampler, batch_size= 64)

In [6]:
geo_distilbert_vecs[:2]

tensor([[-0.7813, -0.0065,  0.5624,  ...,  0.3634, -0.5745,  0.6775],
        [ 0.3635,  0.2143,  0.0812,  ...,  0.3413, -0.4039,  1.0122]])

In [7]:
def sorting( geo_sim_dict, pmid_ls, top_threshold =10):

    '''
    for each geo_id, give a list of recommendations 
    this could be for non-reranking or reranking
    '''
    geo_sim_dict = dict(geo_sim_dict)
    similarity_dict = defaultdict()
    sim_np = np.asarray(list(geo_sim_dict.values()))
    idx_np = np.argsort(sim_np, axis= 1) #so the small values will be in front 
    #take on # of top_threshold
    idx_np = idx_np[:,:top_threshold]
    sim_np_taketop = np.take_along_axis(sim_np, idx_np, axis=1) 
    for i, geo_id in enumerate(geo_sim_dict):
        print('working!')
        pmid_selected = list(np.take(pmid_ls, idx_np[i]))
        selected = dict(zip(pmid_selected, sim_np_taketop[i]))
        similarity_dict[geo_id] = selected     
    return similarity_dict

In [8]:
from Evaluation.find_ranking_citation import CitationRanking
from Evaluation.write_result import WriteResult
from data_loading import DataLoading
from Evaluation.mean_reciprocal_ranking import MRR
from Evaluation.eval_Ginny import Metrics      
    
    
#self.rec_conf = Rec_configuration()
_, _, _, _, citation_data = DataLoading().get_all_details() #we should get actual citations
auto_rank = CitationRanking(citation_data)
write_res = WriteResult()
     

Lemmatization is false, if required turn on again
Loading all geo related preprocessed datasets
Loaded all geo related processed datasets
Loading all title and abstract
Loaded all title and abstract


In [10]:
import os
device  = torch.device("cuda" if torch.cuda.is_available() else "cpu")
for step, batch in enumerate(geo_distilbert_vecs_dataloader):
    #print(batch)
    batch = batch[0].to(device)
    print(batch.shape)
    geo_ids_batch = geo_ids[step*b_size: (step+1)*b_size]
    #geo_batch, geo_ids_batch = batch
    similarity_value_dict = defaultdict()
    #similarity_scores = linear_kernel(geo_bert_vecs, bert_vecs)
    similarity_scores = torch.cdist(batch, distilbert_vecs)  
        #we need to export this value
    np.save(res_addr + 'similarity_scores_batch_' + str(step), similarity_scores.cpu().numpy())
    #load this later
    #np.load(self.res_addr + 'base/similarity_scores')
    print(similarity_scores.shape)
    #call the re-ranking or not 
    for i, geo_id in enumerate(geo_ids_batch): #this is only from testing geo_id
        #print(geo_id)
        #print(geo_id)
        similarity_value_dict[geo_id] =  list(similarity_scores[i].cpu().numpy())
        #similarity_value_dict[geo_id] = scipy.spatial.distance.cdist([geo_bert_vecs[i]], bert_vecs, "cosine")[0]
        '''
        if self.rerank:
        new_similarity_dict = self.re_rank_bert(geo_sim_dict = similarity_value_dict,
                                                   article_title = new_article_title,
                                                   geo_title = new_geo_title, 
                                                   pmid_ls = pmids)
        '''
    new_similarity_dict =  sorting(geo_sim_dict = similarity_value_dict, pmid_ls = pmids)
    new_similarity_dict = dict(new_similarity_dict)
    filename =  res_addr + 'new_similarity_dict_batch_' + str(step)
    os.makedirs(os.path.dirname(filename), exist_ok=True)
    with open(res_addr + 'new_similarity_dict_batch_' + str(step), 'wb') as handle:
        pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)
     

    for id, geo_id in enumerate(geo_ids_batch): 
        temp_selected = new_similarity_dict[geo_id]
        write_res.write(res_addr  + geo_id + '.txt', temp_selected)
        auto_rank.find_citations(geo_id, list(temp_selected.keys())) #keys are a list of pmids

a, b, c, d = auto_rank.get_values() #need to modify this 
print('good geo recommendations = {}, top1 hit geo recommendations = {}, bad geo recommendations = {}, '
      'geo without citations = {}'.format(a, b, c, d))
#we need many more than just MRR

torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
workin

working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!

working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!

working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
workin

working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
workin

...

working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torc

working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
workin

working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
workin

torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([64, 768])
torch.Size([64, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
w

working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
torch.Size([32, 768])
torch.Size([32, 770525])
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
working!
good geo recommendations = 35986, top1 hit geo recommendations = 30331, bad geo recommendations = 40078, geo without citations = 0


In [11]:
print(step)

1188


In [12]:
#import glob
#files = glob.glob(res_addr + "similarity_scores_batch_*")
new_similarity_dict =  {}
#print
#for file in files:
for i in range(step +1):
    with open(res_addr + "new_similarity_dict_batch_" + str(i), 'rb') as fp:
        dict_batch = pickle.load(fp)
        new_similarity_dict.update(dict_batch)
#dict.update(dict2)
#dict.update(dict3)
with open(res_addr + 'new_similarity_dict.pickle', 'wb') as handle:
    pickle.dump(new_similarity_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [14]:
#MRR 
print('MRR:')
print(Metrics(citation_data).calculate_mrr(new_similarity_dict)) #mrr
#recall @1 and recall @10
print('recall@1, recall@10:')
print(Metrics(citation_data).calculate_recall_at_k(new_similarity_dict, 1))
print(Metrics(citation_data).calculate_recall_at_k(new_similarity_dict, 10))
#Precision@1 and precision10
print('precision@1, precision@10:')
print(Metrics(citation_data).calculate_precision_at_k(new_similarity_dict, 1))        
print(Metrics(citation_data).calculate_precision_at_k(new_similarity_dict, 10))
#MAP@10
print(Metrics(citation_data).calculate_MAP_at_k(new_similarity_dict))

MRR:
0.4216038154586614
recall@1, recall@10:
0.3917960533235171
0.46540073709858365
precision@1, precision@10:
0.3987563104753891
0.04753365586874211
0.4213286660022304


In [ ]:


#we use the cosine-similarity and calculate again

In [19]:
import numpy as np
rs = np.array([[0, 0, 0], [0, 1, 0], [1, 0, 0]])
    
r = np.asarray(rs)[:,:3]


In [24]:
r.shape[0]

3

In [40]:
def precision_at_k(r, k):
    """Score is precision @ k
    Relevance is binary (nonzero is relevant).
    >>> r = [0, 0, 1]
    >>> precision_at_k(r, 1)
    0.0
    >>> precision_at_k(r, 2)
    0.0
    >>> precision_at_k(r, 3)
    0.33333333333333331
    >>> precision_at_k(r, 4)
    Traceback (most recent call last):
        File "<stdin>", line 1, in ?
    ValueError: Relevance score length < k
    Args:
        r: Relevance scores (list or numpy) in rank order
            (first element is the first item)
    Returns:
        Precision @ k
    Raises:
        ValueError: len(r) must be >= k
    """
    assert k >= 1
    r = np.asarray(r)[:k] != 0
    if r.size != k:
        raise ValueError('Relevance score length < k')
    return np.mean(r)

In [41]:
def average_precision( r):
    """Score is average precision (area under PR curve)
    Relevance is binary (nonzero is relevant).
    >>> r = [1, 1, 0, 1, 0, 1, 0, 0, 0, 1]
    >>> delta_r = 1. / sum(r)
    >>> sum([sum(r[:x + 1]) / (x + 1.) * delta_r for x, y in enumerate(r) if y])
    0.7833333333333333
    >>> average_precision(r)
    0.78333333333333333
    Args:
        r: Relevance scores (list or numpy) in rank order
            (first element is the first item)
    Returns:
        Average precision
    """
    r = np.asarray(r) != 0
    out = [precision_at_k(r, k+1) for k in range(r.size) if r[k]]
    if not out:
        return 0.
    return np.mean(out)


def mean_average_precision(rs):
    """Score is mean average precision
    Relevance is binary (nonzero is relevant).
    >>> rs = [[1, 1, 0, 1, 0, 1, 0, 0, 0, 1]]
    >>> mean_average_precision(rs)
    0.78333333333333333
    >>> rs = [[1, 1, 0, 1, 0, 1, 0, 0, 0, 1], [0]]
    >>> mean_average_precision(rs)
    0.39166666666666666
    Args:
        rs: Iterator of relevance scores (list or numpy) in rank order
            (first element is the first item)
    Returns:
        Mean average precision
    """
    return np.mean([average_precision(r) for r in rs])

In [43]:
rs =[[1,0,1,0,0,1,0,0,1,1],[0,1,0,0,1,0,1,0,0,0]]
mean_average_precision(rs)

0.5325396825396824

In [15]:
!pip install ml_metrics

  Created wheel for ml-metrics: filename=ml_metrics-0.1.4-cp36-none-any.whl size=7850 sha256=96795382798a55ae73165a93816a845e2ccbdfdfeb87b426f39cdb807f141d0f
  Stored in directory: /home/jzhu/.cache/pip/wheels/b3/61/2d/776be7b8a4f14c5db48c8e5451451cabc58dc6aa7ee3801163
Successfully built ml-metrics


In [17]:
import ml_metrics as metrics
metrics.mapk(actual =[[1,1,1,1,1,0,0,0,0,0],[1,1,1,0,0,0,0,0,0,0]],predicted = [[1,0,1,0,0,1,0,0,1,1],[0,1,0,0,1,0,1,0,0,0]], k=10)

0.2

In [9]:
#semantic match problem:
embedder = SentenceTransformer('bert-base-nli-mean-tokens')

# Corpus with example sentences
corpus = ['A man is eating a food.',
          'A man is eating a piece of bread.',
          'The girl is carrying a baby.',
          'A man is riding a horse.',
          'A woman is playing violin.',
          'Two men pushed carts through the woods.',
          'A man is riding a white horse on an enclosed ground.',
          'A monkey is playing drums.',
          'A cheetah is running behind its prey.']

corpus_embeddings = embedder.encode(corpus)



In [13]:
queries = ['A man is eating pasta.', 
           'Someone in a gorilla costume is playing a set of drums.', 
           'A cheetah chases prey on across a field.']
query_embeddings = embedder.encode(queries)


In [16]:
for query, query_embedding in zip(queries, query_embeddings):
    distances = scipy.spatial.distance.cdist([query_embedding], corpus_embeddings, "cosine")[0]
    print(distances)

[0.21805187 0.15202329 1.04767417 0.8939238  0.96026714 0.79048635
 0.84144166 0.80550682 0.9036305 ]
[0.80833945 0.80898164 0.7649333  0.7976688  0.92636557 0.8432146
 0.8036548  0.20152866 0.7140349 ]
[0.97539467 0.95483552 0.87328062 0.70701557 0.94015294 0.63376357
 0.72819947 0.69392712 0.09933376]


In [15]:
distances

array([0.97539467, 0.95483552, 0.87328062, 0.70701557, 0.94015294,
       0.63376357, 0.72819947, 0.69392712, 0.09933376])